In [ ]:
from tqdm import tqdm
from pymatgen.core import  Structure
import joblib, json
import numpy as np
from ase.io import read
import numpy as np
import sys, os
from pymatgen.io.ase import AseAtomsAdaptor
from pymatgen.core import Structure
from pymatgen.symmetry.analyzer import SpacegroupAnalyzer
import torch
from dis_csp.model import CrystalDataset, VAE
from dis_csp.generation import decode_samples, generate_wyckoffgene, get_cif_lines
from dis_csp.csp_filter import structure_validity,oxidation_state_validity
from io import StringIO

2025-07-18 16:30:21.779866: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-18 16:30:21.785642: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2025-07-18 16:30:21.824009: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-07-18 16:30:21.824060: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-07-18 16:30:21.824097: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to regi

In [ ]:
#latent_space_path = 'Decoded_data/z_samples_kde.npy'
latent_space_path = 'Decoded_data/z_sample_NewICSD_test.npy'
model_dir = 'New_Kl5_ICSD_dis_site_middle_KL_element1000_lr_5e-06_epochs_2500_batch_64_test_0.2_val_0.1'
best_model = True
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

### Load the VAE model ###
if best_model:
    vae_dict = torch.load(model_dir+'/best_vae_model.pth',map_location=torch.device('cpu'))
else: # use exit model
    vae_dict = torch.load(model_dir+'/exit_vae_model.pth',map_location=torch.device('cpu'))

feature_dim = 183
wyckoff_dim = 9
crystal_dim = 236
kernel = [5,3,2]
stride = [2,3,2]
max_filter = 16
latent_dim = 256
vae_eval = VAE(feature_dim, wyckoff_dim, crystal_dim,verbose=False,kernel=kernel,stride=stride)
vae_eval.load_state_dict(vae_dict['model'])

# Decode the latent space samples
#latent_space_path = 'Decoded_data/z_samples_kde_optimized.npy'
cif_save_path = 'Decoded_data/Generated_cif'
print(f"Loading latent space samples from {latent_space_path}")
z_samples = np.load(latent_space_path)

if 'Y_scaler' in vae_dict:
    scaler_Y = vae_dict['Y_scaler']
else:
    # Load the scaler if not present in the model dictionary
    print('Loading Y_scaler from file Y_scaler.gz')
    scaler_Y = joblib.load('Y_scaler.gz')

### Load the latent space samples ###
z_samples = np.load(latent_space_path)

# Get the decoded samples
save_dict = decode_samples(z_samples,vae_eval,scaler_Y,device='cpu')
print('Decoded samples shape:', len(save_dict['spacegroup']))

Loading latent space samples from /home/energy/mahpe/Published_code/Dis-CSP/Decoded_data/z_sample_NewICSD_test.npy
Loading Y_scaler from file Y_scaler.gz
Decoded samples shape: 27008


/home/energy/mahpe/Published_code/Dis-CSP/dis_csp/generation.py:145: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  'disordered_site': F.sigmoid(torch.tensor(disordered_site)).cpu().detach().numpy(),


In [3]:
# Generate Wyckoff genes
mixiter = 1000
element_acc = 0.05  
disorder_acc = 0.5
all_wyckoffgenes,sma_int, failed_int = generate_wyckoffgene(save_dict,
                             max_iter=mixiter,
                             element_acc=element_acc,
                             disorder_acc=disorder_acc,
                             shift_frac_coord=True,
                             verbose=False)
if mixiter is not None:
    print(f"Symmetry Matching Accuracy: {100-sma_int/mixiter*100:.2f}%")
    print(f"Number of failed items: {failed_int} of {mixiter} processed, Procentage: {100-failed_int/mixiter*100:.2f}%")
else:
    print(f"Symmetry Matching Accuracy: {100- sma_int/len(save_dict['spacegroup'])*100:.2f}%")
    print(f"Number of failed items: {failed_int} of {len(save_dict['spacegroup'])} processed, Procentage: {100-failed_int/len(save_dict['spacegroup'])*100:.2f}%")


  4%|▎         | 1000/27008 [02:12<57:35,  7.53it/s] 

Symmetry Matching Accuracy: 98.60%
Number of failed items: 0 of 1000 processed, Procentage: 100.00%


In [4]:
print(f"Number of failed items: {failed_int} of {len(save_dict['spacegroup'])} processed, Procentage: {100-failed_int/len(save_dict['spacegroup'])*100:.2f}%")

Number of failed items: 0 of 27008 processed, Procentage: 100.00%


In [5]:
from io import StringIO
from pymatgen.io.cif import CifParser
len_all_structures = len(save_dict['spacegroup'])


def split_wyckoff(site):
    """
    Split the Wyckoff site into multiplicity and letter.
    
    Args:
        site (str): The Wyckoff site string (e.g., '2a', '3b').
    
    Returns:
        tuple: A tuple containing the multiplicity (int) and the letter (str).
    """
    for i, c in enumerate(site):
        if c.isalpha():
            return int(site[:i]), site[i:]
        

def get_cif_lines(wyckoffgene_dict):
    """
    Generate CIF lines from a wyckoffgene dictionary.

    Args:
        wyckoffgene_dict (dict): Dictionary containing crystal structure information with keys 'spacegroup_group', 'lattice', 'sites', 'species', 'frac_coord', and 'occupancy'.
    
    Returns:
        str: A string containing the CIF lines.
    """

    # Initiate the cif lines
    lines = ""
    # Symmetry information
    spg_group = wyckoffgene_dict['spacegroup_group']
    l_type =spg_group.lattice_type
    number = spg_group.number
    G1 = spg_group[0]
    symbol =spg_group.symbol #if G1.is_standard_setting()

    lines += "data_\n"

    lines += f"\n_symmetry_space_group_name_H-M '{symbol:s}'\n"
    lines += f"_symmetry_Int_Tables_number      {number:>15d}\n"
    lines += f"_symmetry_cell_setting           {l_type:>15s}\n"

    a, b, c, alpha, beta, gamma = wyckoffgene_dict['lattice'].get_para(degree=True)
    lines += f"_cell_length_a        {a:12.1f}\n"
    lines += f"_cell_length_b        {b:12.1f}\n"
    lines += f"_cell_length_c        {c:12.1f}\n"
    lines += f"_cell_angle_alpha     {alpha:12.1f}\n"
    lines += f"_cell_angle_beta      {beta:12.1f}\n"
    lines += f"_cell_angle_gamma     {gamma:12.1f}\n"
    lines += f"_cell_volume          {wyckoffgene_dict['lattice'].volume:12.3f}\n"
    lines += "\nloop_\n"
    lines += " _symmetry_equiv_pos_site_id\n"
    lines += " _symmetry_equiv_pos_as_xyz\n"
    for i, op in enumerate(G1):
        lines += f"{i + 1:d} '{op.as_xyz_str():s}'\n"

    lines += "\nloop_\n"
    lines += " _atom_site_label\n"
    lines += " _atom_site_type_symbol\n"
    lines += " _atom_site_symmetry_multiplicity\n"
    lines += " _atom_site_Wyckoff_symbol\n" # ICSD style
    lines += " _atom_site_fract_x\n"
    lines += " _atom_site_fract_y\n"
    lines += " _atom_site_fract_z\n"
    lines += " _atom_site_occupancy\n"
    #print(wyckoffgene_dict['sites'])
    count= {}
    for i in range(len(wyckoffgene_dict['sites'])):
        wp_list = wyckoffgene_dict['sites'][i]
        for wp_site in wp_list:
            # Split the Wyckoff site into multiplicity and letter
            mul, letter = split_wyckoff(wp_site)
            
            specie = wyckoffgene_dict["species"][i]
            coord = wyckoffgene_dict['frac_coord'][specie][wp_site]
            occ = wyckoffgene_dict['occupancy'][specie][wp_site]

            if len(coord) >1: # if there are 2 frac coordinates at the same site for the same element. Exp. S is at 6c, twich
                if specie not in count.keys():
                    count[specie] = {wp_site: 0}
                else:
                    if wp_site not in count[specie].keys():
                        count[specie][wp_site] = 0

                coord_i = coord[count[specie][wp_site]]
                occ_i = occ[count[specie][wp_site]]
                count[specie][wp_site] += 1
            else:
                coord_i = coord[0]
                occ_i = occ[0]


            lines += f"{specie:6s} {specie:6s} {mul:3d} {letter:s}"
            lines += "{:12.3f}{:12.3f}{:12.3f}".format(*coord_i)
            lines += f" {occ_i} \n"

            
    lines += "#END\n\n"
    return lines

def generate_cif_files(all_wyckoffgenes_list,maxiter=None, validity_check=True,charge_neutral=True,
                       two_oxidation_state=False,validity_primitive=False,symmetry_analyzer=False, verbose=False):
    """
    Generate CIF files from a list of WyckoffGene dictionaries.
    Parameters:
    all_wyckoffgenes_list (list): List of WyckoffGene dictionaries.
    maxiter (int): Maximum number of structures to process. If None, process all.
    validity_check (bool): If True, check the validity of the structures.
    charge_neutral (bool): If True, check the oxidation state validity.
    two_oxidation_state (bool): If True, allow two oxidation states.
    validity_primitive (bool): If True, use the primitive structure for validity checks.
    symmetry_analyzer (bool): If True, use pymatgen's symmetry analyzer.
    verbose (bool): If True, print additional information.
    Returns:
    all_cif_lines (list): List of CIF lines for valid structures.
    cif_lines_wyckoffgene (list): List of CIF lines with corresponding WyckoffGene dictionaries.
    """

    all_cif_lines = []
    cif_lines_wyckoffgene = []
    failed_count = 0
    sym_count = 0
    validity_count = 0
    oxidation_state_count = 0
    validity_count_list = []

    struc_valid = True # If they are not chossen as input, they are valid by default
    oxidation_valid = True # If they are not chossen as input, they are valid by default
    if maxiter is not None:
        print(f"Processing {maxiter} structures out of {len(all_wyckoffgenes_list)}")

    for i in tqdm(range(len(all_wyckoffgenes_list))):
        if maxiter is not None:
            if i >= maxiter:
                break
        wyckoffgene = all_wyckoffgenes_list[i]

        cif_lines = get_cif_lines(wyckoffgene)
        

        try:
            # primitve cell
            if validity_primitive:
                structure = wyckoffgene['structure_pymatgen']
            # Unit cell
            else:
                # Found that pymatgen had some unknown issues readin some cif files, while ase had no errors. Since the efficiency only increased by 10% we will do it with ase
                #structure = Structure.from_str(cif_lines,fmt='cif')
                #cif_file = StringIO(cif_lines)
                #atoms = read(cif_file, format="cif")
                #structure = AseAtomsAdaptor.get_structure(atoms)
                #parser = CifParser.from_str(cif_lines, frac_tolerance=1e-2)
                parser= CifParser.from_str(cif_lines, frac_tolerance=1e-2) #
                struct = parser.parse_structures(primitive=False)[0]
                structure = Structure.from_sites(struct, properties=struct.properties)

        except:
            failed_count += 1
            continue

        if symmetry_analyzer:
            try:
                sga = SpacegroupAnalyzer(structure,symprec=0.01)
                refined_struc = sga.get_refined_structure()
                sga = SpacegroupAnalyzer(refined_struc,symprec=0.01)
                structure = sga.get_symmetrized_structure()
            except:
                sym_count +=1
                continue
        
        if validity_check:
            struc_valid =structure_validity(structure)
            if not struc_valid:
                validity_count += 1
        
        if charge_neutral:   
            oxidation_valid = oxidation_state_validity(wyckoffgene['structure_pymatgen'],two_oxidation_state=two_oxidation_state,verbose=verbose) # pymatgen gets the composition correctly
            if not oxidation_valid:
                oxidation_state_count += 1
    
        # if one of them is not valid, skip the structures
        if not struc_valid:
            continue 
        if not oxidation_valid:
            continue

        # Add the structure to the list
        all_cif_lines.append(cif_lines)
        cif_lines_wyckoffgene.append(wyckoffgene)

    if maxiter is not None:
        print(f'Failed to parse {failed_count} structures out of {maxiter} Procentage: {100-failed_count/maxiter*100:.2f}%')
        if symmetry_analyzer:
            print(f'Pymatgen Symmetry failed for {sym_count} structures out of {maxiter} Procentage: {100-sym_count/maxiter*100:.2f}%')
        if validity_check:
            print(f'Validity check failed for {validity_count} structures out of {maxiter} Procentage: {100-validity_count/maxiter*100:.2f}%')
        if charge_neutral:
            print(f'Oxidation state check failed for {oxidation_state_count} structures out of {maxiter} Procentage: {100-oxidation_state_count/maxiter*100:.2f}%')
        print(f'Total valid structures: {len(all_cif_lines)} out of {maxiter} Procentage: {len(all_cif_lines)/maxiter*100:.2f}%')
    else:
        print(f"Failed to parse {failed_count} structures out of {len(all_wyckoffgenes_list)} Procentage: {100-failed_count/len(all_wyckoffgenes_list)*100:.2f}%")
        if symmetry_analyzer:
            print(f"Pymatgen Symmetry failed for {sym_count} structures out of {len(all_wyckoffgenes_list)} Procentage: {100-sym_count/len(all_wyckoffgenes_list)*100:.2f}%")
        if validity_check:
            print(f"Validity check failed for {validity_count} structures out of {len(all_wyckoffgenes_list)} Procentage: {100-validity_count/len(all_wyckoffgenes_list)*100:.2f}%")
        if charge_neutral:
            print(f"Oxidation state check failed for {oxidation_state_count} structures out of {len(all_wyckoffgenes_list)} Procentage: {oxidation_state_count/len(all_wyckoffgenes_list)*100:.2f}%")
        print(f"Total valid structures: {len(all_cif_lines)} out of {len(all_wyckoffgenes_list)} Procentage: {len(all_cif_lines)/len(all_wyckoffgenes_list)*100:.2f}%")    

    return all_cif_lines, cif_lines_wyckoffgene


In [71]:
len_all_structures = len(save_dict['spacegroup'])
all_cifs,cifs__wyckoffgene = generate_cif_files(all_wyckoffgenes,maxiter=len_all_structures,validity_primitive=False,symmetry_analyzer=True, verbose=False, two_oxidation_state=False)

Processing 27008 structures out of 26571


  0%|          | 0/26571 [00:00<?, ?it/s]/tmp/ipykernel_3391485/4047180129.py:158: UserWarning: Issues encountered while parsing CIF: Skipping relative stoichiometry check because CIF does not contain formula keys.
  struct = parser.parse_structures(primitive=False)[0]
/tmp/ipykernel_3391485/4047180129.py:158: UserWarning: Issues encountered while parsing CIF: Skipping relative stoichiometry check because CIF does not contain formula keys.
  struct = parser.parse_structures(primitive=False)[0]
  0%|          | 3/26571 [00:00<15:21, 28.84it/s]/tmp/ipykernel_3391485/4047180129.py:158: UserWarning: Issues encountered while parsing CIF: 4 fractional coordinates rounded to ideal values to avoid issues with finite precision.
Skipping relative stoichiometry check because CIF does not contain formula keys.
  struct = parser.parse_structures(primitive=False)[0]
/tmp/ipykernel_3391485/4047180129.py:158: UserWarning: Issues encountered while parsing CIF: Skipping relative stoichiometry check beca

Failed to parse 55 structures out of 27008 Procentage: 99.80%
Pymatgen Symmetry failed for 1860 structures out of 27008 Procentage: 93.11%
Validity check failed for 5791 structures out of 27008 Procentage: 78.56%
Oxidation state check failed for 10956 structures out of 27008 Procentage: 59.43%
Total valid structures: 10613 out of 27008 Procentage: 39.30%


In [ ]:
parser = CifParser.from_str(cif_lines,occupancy_tolerance=2, frac_tolerance=1e-2)
parser.parse_structures(primitive=False)[0]

TypeError: CifParser.get_lattice() missing 1 required positional argument: 'data'

In [73]:
wyckoffgene

{'spacegroup': 166,
 'species': ['Ba', 'V', 'O'],
 'sites': [['3a', '6c'], ['6c'], ['6c', '18h']],
 'numIons': [9, 6, 24],
 'lattice':   5.8154,   5.7935,  21.2996,  89.9277,  89.8745, 119.7572, trigonal,
 'occupancy': defaultdict(<function dis_csp.generation.generate_wyckoffgene.<locals>.<lambda>()>,
             {'Ba': defaultdict(list, {'3a': [1.0], '6c': [1.0]}),
              'V': defaultdict(list, {'6c': [1.0]}),
              'O': defaultdict(list, {'6c': [1.0], '18h': [1.0]})}),
 'frac_coord': defaultdict(<function dis_csp.generation.generate_wyckoffgene.<locals>.<lambda>()>,
             {'Ba': defaultdict(list,
                          {'3a': [array([0., 0., 0.])],
                           '6c': [array([0.66666667, 0.33333333, 0.33333333])]}),
              'V': defaultdict(list,
                          {'6c': [array([0.32814175, 0.66024753, 0.18554929])]}),
              'O': defaultdict(list,
                          {'6c': [array([0.66666667, 0.33333333, 0.33333333])

In [78]:
for i, op in enumerate(Group(166)):
    print(type(op))

<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>
<class 'pyxtal.symmetry.Wyckoff_position'>


In [76]:
from pyxtal import Group
Group(166).__dir__()

['string',
 'dim',
 'header',
 'symbol',
 'number',
 'PBC',
 'lattice_type',
 'lattice_id',
 'point_group',
 'pg_number',
 'polar',
 'inversion',
 'chiral',
 'hall_number',
 'P',
 'P1',
 'wyckoffs',
 'w_symm',
 'Wyckoff_positions',
 'wyckoffs_organized',
 '__module__',
 '__doc__',
 '__init__',
 '_initialize_hall_data',
 '_initialize_wyckoff_data',
 '__str__',
 '__repr__',
 '__iter__',
 '__getitem__',
 '__len__',
 'get_ferroelectric_groups',
 'get_site_dof',
 'get_spg_representation',
 'get_lattice_id',
 'get_lattice_dof',
 'is_valid_combination',
 'list_wyckoff_combinations',
 'get_spg_symmetry_object',
 'get_wyckoff_position',
 'get_wyckoff_position_from_xyz',
 'get_alternatives',
 '_get_max_k_subgroup',
 '_get_max_t_subgroup',
 'get_max_k_subgroup',
 'get_max_t_subgroup',
 'get_max_subgroup',
 'get_wp_list',
 'get_splitters_from_structure',
 'get_splitters_from_relation',
 'get_min_supergroup',
 '_get_max_subgroup_numbers',
 'get_max_subgroup_numbers',
 'get_lists',
 'get_lists_mol',

In [27]:
wyckoffgene['frac_coord']

defaultdict(<function dis_csp.generation.generate_wyckoffgene.<locals>.<lambda>()>,
            {'Ce': defaultdict(list,
                         {'4e': [array([0.5       , 0.5       , 0.30256617])]}),
             'Nd': defaultdict(list,
                         {'4e': [array([0.5       , 0.5       , 0.30256617])]}),
             'Cu': defaultdict(list, {'2a': [array([0., 0., 0.])]}),
             'O': defaultdict(list,
                         {'4c': [array([0.5, 0. , 0. ])],
                          '4d': [array([0.  , 0.5 , 0.25])]})})

In [6]:
wyckoffgene['structure_pymatgen']

Structure Summary
Lattice
    abc : 3.900000095367435 3.9000000953674347 12.0
 angles : 90.00000250447812 90.00000250447812 90.00000250447816
 volume : 182.5200089263915
      A : 3.9000000953674316 0.0 -1.7047442213424802e-07
      B : -1.704744325813105e-07 3.9000000953674276 -1.7047442213424802e-07
      C : 0.0 0.0 12.0
    pbc : True True True
PeriodicSite: Ce:0.06, Nd:0.88 (1.95, 1.95, 3.631) [0.5, 0.5, 0.3026]
PeriodicSite: Cu (0.0, 0.0, 0.0) [0.0, 0.0, 0.0]
PeriodicSite: O (1.95, 0.0, -8.524e-08) [0.5, 0.0, 0.0]
PeriodicSite: O (-8.524e-08, 1.95, 3.0) [0.0, 0.5, 0.25]

['e', 'a', 'c', 'd']

In [ ]:
wyckoffgene['wyckoff_sites_list']

['4e', '2a', '4c', '4d']

In [ ]:
from pymatgen.symmetry.structure import SymmetrizedStructure
from pymatgen.symmetry.analyzer import SpacegroupOperations
from pymatgen.symmetry.groups import SpaceGroup
from pymatgen.util.coord import in_coord_list

count_valid = 0

for wyckoffgene in all_wyckoffgenes:
    full_structure = wyckoffgene['structure_pymatgen']
    letters = [ split_wyckoff(site)[-1] for site in wyckoffgene['wyckoff_sites_list']]
    mult = [ split_wyckoff(site)[0] for site in wyckoffgene['wyckoff_sites_list']]
    spg_int = wyckoffgene['spacegroup']
    sym_ops = SpaceGroup.from_int_number(spg_int).symmetry_ops   # Obtains a SpaceGroup from its international number

    full_coords = []
    full_species = []

    # Loop through the sites and apply symmetry operations    
    for site in full_structure.sites:
        for sym_op in sym_ops:
            transformed_coords = sym_op.operate(site.frac_coords) % 1  # bring back to unit cell
            species = site.species
            full_coords.append(transformed_coords)
            full_species.append(species)
    
    # Remove duplicates
    unique_coords = []
    unique_species = []
    tolerance = 0.01
    for i, coord in enumerate(full_coords):
        if not in_coord_list(unique_coords, coord, atol=tolerance):
            unique_coords.append(coord)
            unique_species.append(full_species[i])

    full_structure = Structure(full_structure.lattice, unique_species, unique_coords)

    if structure_validity(full_structure):
        count_valid += 1
    #symm_struct = SymmetrizedStructure(
    #    structure=full_structure,
    #    spacegroup=SpacegroupOperations(SpaceGroup.from_int_number(spg_int).full_symbol, spg_int, sym_ops),
    #    equivalent_positions=mult,
    #    wyckoff_letters=letters
    #)
    

In [17]:
mult

[4, 2, 4, 4]

In [19]:
symm_struct

SymmetrizedStructure
Full Formula (Ce0.24 Nd3.52 Cu2 O8)
Reduced Formula: Ce0.24Nd3.52Cu2O8
Spacegroup: I4/m2/m2/m (139)
abc   :   3.900000   3.900000  12.000000
angles:  90.000003  90.000003  90.000003
Sites (14)
  #  SP                  a    b         c  Wyckoff
---  ----------------  ---  ---  --------  ---------
  0  Ce:0.06, Nd:0.88  0.5  0.5  0.302566  1a
  1  Ce:0.06, Nd:0.88  0.5  0.5  0.697434  3e

In [21]:
get_cif_lines(wyckoffgene).split('\n')

['data_',
 '',
 "_symmetry_space_group_name_H-M 'I4/mmm'",
 '_symmetry_Int_Tables_number                  139',
 '_symmetry_cell_setting                tetragonal',
 '_cell_length_a                 3.9',
 '_cell_length_b                 3.9',
 '_cell_length_c                12.0',
 '_cell_angle_alpha             90.0',
 '_cell_angle_beta              90.0',
 '_cell_angle_gamma             90.0',
 '_cell_volume               182.520',
 '',
 'loop_',
 ' _symmetry_equiv_pos_site_id',
 ' _symmetry_equiv_pos_as_xyz',
 "1 'x, y, z'",
 "2 '-x, -y, z'",
 "3 '-y, x, z'",
 "4 'y, -x, z'",
 "5 '-x, y, -z'",
 "6 'x, -y, -z'",
 "7 'y, x, -z'",
 "8 '-y, -x, -z'",
 "9 '-x, -y, -z'",
 "10 'x, y, -z'",
 "11 'y, -x, -z'",
 "12 '-y, x, -z'",
 "13 'x, -y, z'",
 "14 '-x, y, z'",
 "15 '-y, -x, z'",
 "16 'y, x, z'",
 "17 'x+1/2, y+1/2, z+1/2'",
 "18 '-x+1/2, -y+1/2, z+1/2'",
 "19 '-y+1/2, x+1/2, z+1/2'",
 "20 'y+1/2, -x+1/2, z+1/2'",
 "21 '-x+1/2, y+1/2, -z+1/2'",
 "22 'x+1/2, -y+1/2, -z+1/2'",
 "23 'y+1/2, 

In [20]:
full_structure

Structure Summary
Lattice
    abc : 3.900000095367435 3.9000000953674347 12.0
 angles : 90.00000250447812 90.00000250447812 90.00000250447816
 volume : 182.5200089263915
      A : 3.9000000953674316 0.0 -1.7047442213424802e-07
      B : -1.704744325813105e-07 3.9000000953674276 -1.7047442213424802e-07
      C : 0.0 0.0 12.0
    pbc : True True True
PeriodicSite: Ce:0.06, Nd:0.88 (1.95, 1.95, 8.369) [0.5, 0.5, 0.6974]
PeriodicSite: Ce:0.06, Nd:0.88 (1.95, 1.95, 3.631) [0.5, 0.5, 0.3026]
PeriodicSite: Ce:0.06, Nd:0.88 (0.0, 0.0, 9.631) [0.0, 0.0, 0.8026]
PeriodicSite: Ce:0.06, Nd:0.88 (0.0, 0.0, 2.369) [0.0, 0.0, 0.1974]
PeriodicSite: Cu (0.0, 0.0, 0.0) [0.0, 0.0, 0.0]
PeriodicSite: Cu (1.95, 1.95, 6.0) [0.5, 0.5, 0.5]
PeriodicSite: O (1.95, 0.0, -8.524e-08) [0.5, 0.0, 0.0]
PeriodicSite: O (-8.524e-08, 1.95, -8.524e-08) [0.0, 0.5, 0.0]
PeriodicSite: O (-8.524e-08, 1.95, 6.0) [0.0, 0.5, 0.5]
PeriodicSite: O (1.95, 0.0, 6.0) [0.5, 0.0, 0.5]
PeriodicSite: O (-8.524e-08, 1.95, 9.0) [0.0, 0.5

In [26]:
full_structure

Structure Summary
Lattice
    abc : 3.900000095367435 3.9000000953674347 12.0
 angles : 90.00000250447812 90.00000250447812 90.00000250447816
 volume : 182.5200089263915
      A : 3.9000000953674316 0.0 -1.7047442213424802e-07
      B : -1.704744325813105e-07 3.9000000953674276 -1.7047442213424802e-07
      C : 0.0 0.0 12.0
    pbc : True True True
PeriodicSite: Ce:0.06, Nd:0.88 (1.95, 1.95, 3.631) [0.5, 0.5, 0.3026]
PeriodicSite: Cu (0.0, 0.0, 0.0) [0.0, 0.0, 0.0]
PeriodicSite: O (1.95, 0.0, -8.524e-08) [0.5, 0.0, 0.0]
PeriodicSite: O (-8.524e-08, 1.95, 3.0) [0.0, 0.5, 0.25]

In [22]:
symm_struct

SymmetrizedStructure
Full Formula (Ce0.06 Nd0.88 Cu1 O2)
Reduced Formula: Ce0.06Nd0.88Cu1O2
Spacegroup: I4/m2/m2/m (139)
abc   :   3.900000   3.900000  12.000000
angles:  90.000003  90.000003  90.000003
Sites (4)
  #  SP                  a    b         c  Wyckoff
---  ----------------  ---  ---  --------  ---------
  0  Ce:0.06, Nd:0.88  0.5  0.5  0.302566  1e

In [4]:
from pymatgen.io.cif import CifParser

cutoff = 0.5
count_test = 0
for wyckoffgene in all_wyckoffgenes:
    cif_lines = get_cif_lines(wyckoffgene)
    parser = CifParser.from_str(cif_lines frac_tolerance=1e-2)
    struct = parser.parse_structures(primitive=False)[0]
    structure = Structure.from_sites(struct, properties=struct.properties)
structure.distance_matrix.shape, np.min(structure.distance_matrix + np.diag(np.ones(structure.distance_matrix.shape[0]) * (cutoff + 10.)) )

SyntaxError: invalid syntax. Perhaps you forgot a comma? (2842523331.py, line 7)

In [46]:
cif_lines.split('\n')

['data_',
 '',
 "_symmetry_space_group_name_H-M 'Pn-3'",
 '_symmetry_Int_Tables_number                  201',
 '_symmetry_cell_setting                     cubic',
 '_cell_length_a               9.500',
 '_cell_length_b               9.500',
 '_cell_length_c               9.500',
 '_cell_angle_alpha           90.000',
 '_cell_angle_beta            90.000',
 '_cell_angle_gamma           90.000',
 '_cell_volume               857.375',
 '',
 'loop_',
 ' _symmetry_equiv_pos_site_id',
 ' _symmetry_equiv_pos_as_xyz',
 "1 'x, y, z'",
 "2 '-x+1/2, -y+1/2, z'",
 "3 '-x+1/2, y, -z+1/2'",
 "4 'x, -y+1/2, -z+1/2'",
 "5 'z, x, y'",
 "6 'z, -x+1/2, -y+1/2'",
 "7 '-z+1/2, -x+1/2, y'",
 "8 '-z+1/2, x, -y+1/2'",
 "9 'y, z, x'",
 "10 '-y+1/2, z, -x+1/2'",
 "11 'y, -z+1/2, -x+1/2'",
 "12 '-y+1/2, -z+1/2, x'",
 "13 '-x, -y, -z'",
 "14 'x+1/2, y+1/2, -z'",
 "15 'x+1/2, -y, z+1/2'",
 "16 '-x, y+1/2, z+1/2'",
 "17 '-z, -x, -y'",
 "18 '-z, x+1/2, y+1/2'",
 "19 'z+1/2, x+1/2, -y'",
 "20 'z+1/2, -x, y+1/2'",
 "2

In [72]:
from pymatgen.io.cif import CifParser
from dis_csp.csp_filter import structure_validity,oxidation_state_validity
cif_lines_all = np.load('/home/energy/mahpe/Published_code/dis_gen_all_cifs_test.npy')
cutoff = 0.5
count_test = 0
count_valid = 0
for cif_lines in cif_lines_all:
    try:
        parser = CifParser.from_str(cif_lines,frac_tolerance=1e-2) #CifParser.from_str(cif_lines,occupancy_tolerance=2, frac_tolerance=1e-1)
        struct = parser.parse_structures(primitive=False,symmetrized=True)[0]
    except:
        count_test += 1
        continue
    structure = Structure.from_sites(struct, properties=struct.properties)
    if not structure_validity(structure):
        count_valid += 1
print(f"Count of valid structures: {count_valid} out of {len(cif_lines_all)}")
print(f"Count of failed structures: {count_test} out of {len(cif_lines_all)}")
structure.distance_matrix.shape, np.min(structure.distance_matrix + np.diag(np.ones(structure.distance_matrix.shape[0]) * (cutoff + 10.)) )

/tmp/ipykernel_3391485/4079934109.py:10: UserWarning: Issues encountered while parsing CIF: 1 fractional coordinates rounded to ideal values to avoid issues with finite precision.
  struct = parser.parse_structures(primitive=False,symmetrized=True)[0]
/tmp/ipykernel_3391485/4079934109.py:10: UserWarning: Issues encountered while parsing CIF: 4 fractional coordinates rounded to ideal values to avoid issues with finite precision.
  struct = parser.parse_structures(primitive=False,symmetrized=True)[0]
/home/energy/mahpe/anaconda3/envs/env_sylg/lib/python3.11/site-packages/pymatgen/io/cif.py:1313: UserWarning: Some occupancies ([2.0]) sum to > 1! If they are within the occupancy_tolerance, they will be rescaled. The current occupancy_tolerance is set to: 1.0
  if struct := self._get_structure(data, primitive, symmetrized, check_occu=check_occu):
/tmp/ipykernel_3391485/4079934109.py:10: UserWarning: No structure parsed for section 1 in CIF.
Occupancy 2.0 exceeded tolerance.
  struct = parse

Count of valid structures: 2897 out of 27008
Count of failed structures: 720 out of 27008


((8, 8), 2.6783505670468157)

In [7]:
# make a dictionary with the cif lines and the indexes
cif_dict = {}
for i, cif_lines in enumerate(all_cifs):
    cif_dict[i] = cif_lines

cif_dict_name = latent_space_path.split('/')[-1].replace('.npy','_cif_dict.json')

# Save the cif_dict to a file
cif_dict_path = os.path.join(cif_save_path, cif_dict_name)
with open(cif_dict_path, 'w') as f:
    json.dump(cif_dict, f)

# Save the cif lines to a file
cif_file_path = os.path.join(cif_save_path, latent_space_path.split('/')[-1].replace('.npy',''))
if not os.path.exists(cif_file_path):
    os.makedirs(cif_file_path)


for i, cif_lines in enumerate(all_cifs):
    composition = cifs__wyckoffgene[i]['structure_pymatgen'].composition
    cif_file_name = f'{i}_{composition}_spg_{cifs__wyckoffgene[i]["spacegroup"]}.cif'
    with open(os.path.join(cif_file_path,cif_file_name), 'w') as f:
        f.write(cif_lines)